In [ ]:
from pyspark import SparkConf, SparkContext

In [ ]:
sc.stop()

NameError: name 'sc' is not defined

In [ ]:
conf = SparkConf().setAppName("airline delay Dataset Transformations").setMaster("local")
sc = SparkContext(conf=conf)

In [ ]:
rdd = sc.textFile("/content/airlines_delay.csv")

In [ ]:
rdd= rdd.map(lambda line: line.split(","))

In [ ]:
print(rdd.take(5))

[['Flight', 'Time', 'Length', 'Airline', 'AirportFrom', 'AirportTo', 'DayOfWeek', 'Class'], ['2313.0', '1296.0', '141.0', 'DL', 'ATL', 'HOU', '1', '0'], ['6948.0', '360.0', '146.0', 'OO', 'COS', 'ORD', '4', '0'], ['1247.0', '1170.0', '143.0', 'B6', 'BOS', 'CLT', '3', '0'], ['31.0', '1410.0', '344.0', 'US', 'OGG', 'PHX', '6', '0']]


In [ ]:
rdd.count()

539383

In [ ]:
rdd = rdd.filter(lambda row: row != header)

In [ ]:
rdd = rdd.filter(
    lambda row: any(val is None for val in row)
)

In [ ]:
rdd = sc.textFile("/content/airlines_delay.csv")
header = rdd.first()
rdd = rdd.filter(lambda row: row != header)

In [ ]:
rdd_no_duplicates = rdd.distinct()

In [ ]:
rdd_with_missing = rdd.filter(lambda row: any(val is None or val == '' for val in row))

In [ ]:
print("Rows with missing values:")
for row in rdd_with_missing.take(10):
    print(row)
missing_count = rdd_with_missing.count()
print(f"Total rows with missing values: {missing_count}")

Rows with missing values:
Total rows with missing values: 0


In [ ]:
from pyspark import SparkConf, SparkContext
import numpy as np

rdd = sc.textFile("/content/airlines_delay.csv")
header = rdd.first()
rdd = rdd.filter(lambda row: row != header)
rdd = rdd.map(lambda line: line.split(","))

def detect_outliers(rdd, column_index=3):
    numeric_data = rdd.map(lambda row: float(row[column_index]) if len(row) > column_index and row[column_index] and row[column_index].isdigit() else np.nan).filter(lambda x: not np.isnan(x)).collect()

    if not numeric_data:
        print("No numeric data found for outlier detection in column", column_index)
        return rdd.filter(lambda x: False)

    q1 = np.percentile(numeric_data, 25)
    q3 = np.percentile(numeric_data, 75)
    iqr = q3 - q1

    lower_bound = q1 - 1.5 * iqr
    upper_bound = q3 + 1.5 * iqr

    outliers_rdd = rdd.filter(lambda row: len(row) > column_index and (float(row[column_index]) < lower_bound or float(row[column_index]) > upper_bound))
    return outliers_rdd

outliers_rdd = detect_outliers(rdd)

print("Outliers:")
for row in outliers_rdd.take(10):
    print(row)

outlier_count = outliers_rdd.count()
print(f"Total outliers: {outlier_count}")

No numeric data found for outlier detection in column 3
Outliers:
Total outliers: 0


Transforming functions

In [ ]:
rdd_map = rdd.map(lambda x: (int(float(x[0])) + 1, x[1]))
print("map():")
print(rdd_map.collect())

In [ ]:
rdd_filter = rdd.filter(lambda x: float(x[0]) > 2)
print("\nfilter():")
print(rdd_filter.collect())

In [ ]:
rdd_flatmap = rdd.flatMap(lambda x: (x[0], x[1]))
print("\nflatMap():")
print(rdd_flatmap.collect())

In [ ]:
data2 = [(1, "X"), (2, "Y"), (3, "Z"), (5, "W")]
rdd2 = sc.parallelize(data2)
rdd_distinct = rdd.map(tuple).union(rdd2).distinct()
print("\ndistinct():")
print(rdd_distinct.collect())

In [ ]:
rdd_union = rdd.union(rdd2)
print("\nunion():")
print(rdd_union.collect())

In [ ]:
rdd_intersection = rdd.map(lambda x: tuple(map(str, x))).intersection(rdd2)
print("\nintersection():")
print(rdd_intersection.collect())


intersection():
[]


In [ ]:
rdd_subtract = rdd.map(lambda x: tuple(x)).subtract(rdd2)
print("\nsubtract():")
print(rdd_subtract.collect())

In [ ]:
rdd = sc.textFile("/content/airlines_delay.csv")
header = rdd.first()
rdd = rdd.filter(lambda row: row != header)
rdd = rdd.map(lambda line: line.split(","))
rdd = rdd.map(lambda x: (int(float(x[0])), x[1]))

rdd_group_by_key = rdd.groupByKey()
print("\ngroupByKey():")
print([(k, list(v)) for k, v in rdd_group_by_key.collect()])


groupByKey():
[(2313, ['1296.0', '1132.0', '1135.0', '540.0', '1132.0', '1132.0', '1135.0', '1132.0', '1135.0', '1132.0', '720.0', '955.0', '1135.0', '1135.0', '1296.0', '610.0', '1135.0', '1296.0', '1132.0', '1135.0', '1296.0', '1296.0', '610.0', '1296.0', '450.0', '1135.0', '1135.0', '1296.0', '1132.0', '610.0', '1132.0', '1135.0', '1296.0', '710.0', '1132.0', '1135.0', '1132.0', '1135.0', '1296.0', '720.0', '1132.0', '1296.0', '720.0', '1132.0', '1296.0', '1132.0', '830.0', '1296.0', '1296.0', '1132.0', '1132.0', '1296.0', '1296.0', '1296.0', '610.0', '1296.0', '1132.0', '1132.0', '720.0']), (6948, ['360.0', '410.0', '360.0', '490.0', '490.0', '490.0', '360.0', '490.0', '410.0', '360.0', '410.0', '410.0', '360.0', '490.0', '360.0', '410.0', '490.0', '490.0', '490.0', '360.0', '490.0', '410.0', '490.0', '490.0', '410.0', '360.0', '410.0', '410.0', '490.0', '360.0', '360.0', '410.0', '490.0', '410.0', '360.0', '490.0', '410.0', '410.0', '410.0', '360.0', '410.0', '360.0', '490.0']), 

In [ ]:
rdd_reduce_by_key = rdd.map(lambda x: (x[0], 1)).reduceByKey(lambda x, y: x + y)
print("\nreduceByKey():")
print(rdd_reduce_by_key.collect())


reduceByKey():
[(2313, 59), (6948, 43), (1247, 157), (31, 270), (563, 201), (3692, 96), (1135, 150), (1300, 60), (587, 183), (764, 106), (1147, 161), (1440, 229), (6605, 51), (2670, 91), (1015, 218), (7032, 58), (138, 205), (5411, 25), (2517, 59), (3721, 54), (443, 140), (1689, 110), (2495, 115), (2915, 115), (6304, 54), (969, 59), (1068, 95), (6723, 65), (567, 194), (3005, 62), (1578, 186), (663, 161), (1048, 298), (1214, 105), (2251, 57), (2773, 138), (6321, 106), (536, 129), (1155, 204), (2452, 56), (593, 196), (5117, 61), (152, 234), (239, 249), (4109, 68), (1698, 130), (2744, 93), (6544, 78), (455, 186), (7771, 57), (845, 113), (4865, 14), (4056, 60), (3334, 48), (2722, 108), (6850, 44), (3042, 77), (184, 150), (5423, 60), (2602, 90), (2756, 104), (4064, 29), (4581, 61), (4636, 39), (6353, 56), (936, 147), (6425, 92), (7, 321), (1237, 87), (667, 294), (288, 151), (582, 202), (329, 263), (674, 228), (3647, 31), (780, 81), (1079, 222), (7085, 48), (2439, 116), (3004, 87), (2364, 10

In [ ]:
rdd_join = rdd.join(rdd2)
print("\njoin():")
print(rdd_join.collect())


join():
[(2, ('560.0', 'Y')), (2, ('1025.0', 'Y')), (2, ('855.0', 'Y')), (2, ('390.0', 'Y')), (2, ('400.0', 'Y')), (2, ('390.0', 'Y')), (2, ('390.0', 'Y')), (2, ('560.0', 'Y')), (2, ('585.0', 'Y')), (2, ('855.0', 'Y')), (2, ('855.0', 'Y')), (2, ('855.0', 'Y')), (2, ('1027.0', 'Y')), (2, ('1150.0', 'Y')), (2, ('1035.0', 'Y')), (2, ('1035.0', 'Y')), (2, ('905.0', 'Y')), (2, ('560.0', 'Y')), (2, ('905.0', 'Y')), (2, ('855.0', 'Y')), (2, ('400.0', 'Y')), (2, ('1025.0', 'Y')), (2, ('855.0', 'Y')), (2, ('1035.0', 'Y')), (2, ('905.0', 'Y')), (2, ('540.0', 'Y')), (2, ('855.0', 'Y')), (2, ('475.0', 'Y')), (2, ('1150.0', 'Y')), (2, ('540.0', 'Y')), (2, ('1025.0', 'Y')), (2, ('855.0', 'Y')), (2, ('1035.0', 'Y')), (2, ('390.0', 'Y')), (2, ('475.0', 'Y')), (2, ('855.0', 'Y')), (2, ('855.0', 'Y')), (2, ('560.0', 'Y')), (2, ('1315.0', 'Y')), (2, ('390.0', 'Y')), (2, ('540.0', 'Y')), (2, ('540.0', 'Y')), (2, ('400.0', 'Y')), (2, ('475.0', 'Y')), (2, ('480.0', 'Y')), (2, ('560.0', 'Y')), (2, ('1150.0'

In [ ]:
rdd_cartesian = rdd.cartesian(rdd2)
print("\ncartesian():")
print(rdd_cartesian.collect())

Action method

In [ ]:
print("collect():")
print(rdd.collect())

In [ ]:
print("\ncount():")
print(rdd.count())


count():
539382


In [ ]:
print("\nfirst():")
print(rdd.first())


first():
(2313, '1296.0')


In [ ]:
print("\ntake(2):")
print(rdd.take(2))


take(2):
[(2313, '1296.0'), (6948, '360.0')]


In [ ]:
rdd_numbers = rdd.map(lambda x: x[0])
sum_of_numbers = rdd_numbers.reduce(lambda x, y: x + y)
print("\nreduce():")
print(sum_of_numbers)


reduce():
1309580654


In [ ]:
print("\nforeach():")
rdd.foreach(lambda x: print(f"Element: {x}"))
sc.stop


foreach():


<bound method SparkContext.stop of <SparkContext master=local appName=airline delay Dataset Transformations>>

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
from pyspark import SparkContext
from pyspark.sql import SparkSession

In [ ]:
spark = SparkSession.builder.appName("RDD Analysis and Visualization").getOrCreate()
sc = spark.sparkContext

In [ ]:
price_rdd = rdd.map(lambda x: float(x[1]))
price_stats = price_rdd.stats()

print("Price Statistics:")
print(price_stats)

Price Statistics:
(count: 539382, mean: 802.7281611177052, stdev: 278.0452878417982, max: 1439.0, min: 10.0)


In [ ]:
volume_rdd = rdd.map(lambda x: float(x[2]))
volume_data = volume_rdd.collect()

plt.scatter(price_data, volume_data)
plt.xlabel("Price")
plt.ylabel("Volume")
plt.title("Price vs. Volume")
plt.show()

### DATA FRAME

In [ ]:
!pip install pyspark

## Creating Spark Session

In [ ]:
from pyspark.sql import SparkSession
spark = SparkSession.builder.appName("project").getOrCreate()

## Importing Dataset

In [ ]:
df = spark.read.csv("/content/airlines_delay.csv", header=True, inferSchema=True)
df.show()

+------+------+------+-------+-----------+---------+---------+-----+
|Flight|  Time|Length|Airline|AirportFrom|AirportTo|DayOfWeek|Class|
+------+------+------+-------+-----------+---------+---------+-----+
|2313.0|1296.0| 141.0|     DL|        ATL|      HOU|        1|    0|
|6948.0| 360.0| 146.0|     OO|        COS|      ORD|        4|    0|
|1247.0|1170.0| 143.0|     B6|        BOS|      CLT|        3|    0|
|  31.0|1410.0| 344.0|     US|        OGG|      PHX|        6|    0|
| 563.0| 692.0|  98.0|     FL|        BMI|      ATL|        4|    0|
|3692.0| 580.0|  60.0|     WN|        MSY|      BHM|        4|    0|
|1135.0| 690.0| 239.0|     CO|        EWR|      DFW|        4|    0|
|1300.0|1210.0|  80.0|     AA|        DFW|      MEM|        3|    0|
| 587.0|1295.0| 105.0|     FL|        BWI|      GRR|        7|    0|
| 764.0| 530.0| 108.0|     FL|        ATL|      PBI|        3|    0|
|1147.0|1103.0| 121.0|     FL|        CRW|      MCO|        4|    0|
|1440.0| 951.0|  79.0|     B6|    

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
df.printSchema()

root
 |-- Flight: double (nullable = true)
 |-- Time: double (nullable = true)
 |-- Length: double (nullable = true)
 |-- Airline: string (nullable = true)
 |-- AirportFrom: string (nullable = true)
 |-- AirportTo: string (nullable = true)
 |-- DayOfWeek: integer (nullable = true)
 |-- Class: integer (nullable = true)



## Action

In [ ]:
df.count()

539382

In [ ]:
first_line = df.first()
print(f"First Line: {first_line}")

First Line: Row(Flight=2313.0, Time=1296.0, Length=141.0, Airline='DL', AirportFrom='ATL', AirportTo='HOU', DayOfWeek=1, Class=0)


In [ ]:
df.columns

['Flight',
 'Time',
 'Length',
 'Airline',
 'AirportFrom',
 'AirportTo',
 'DayOfWeek',
 'Class']

In [ ]:
df.na.drop()

DataFrame[Flight: double, Time: double, Length: double, Airline: string, AirportFrom: string, AirportTo: string, DayOfWeek: int, Class: int]

In [ ]:
df.count()

539382

## Transformation

In [ ]:
filtered_df = df.filter(df["Class"] ==0)
filtered_df

DataFrame[Flight: double, Time: double, Length: double, Airline: string, AirportFrom: string, AirportTo: string, DayOfWeek: int, Class: int]

In [ ]:
df.groupBy("Class").count().show()

+-----+------+
|Class| count|
+-----+------+
|    1|240264|
|    0|299118|
+-----+------+



In [ ]:
df.select("Class").distinct().show()

+-----+
|Class|
+-----+
|    1|
|    0|
+-----+



## Importing necessary libraries

In [ ]:
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.feature import IndexToString,StringIndexer

# StringIndexer:Handling categorical variables or strings by converting them into numerical indices.

In [ ]:
indexer=StringIndexer(inputCols=["Airline","AirportFrom","AirportTo"],outputCols=["Airline1","AirportFrom1","AirportTo1"])
indexed=indexer.fit(df).transform(df)
indexed.show()

+------+------+------+-------+-----------+---------+---------+-----+--------+------------+----------+
|Flight|  Time|Length|Airline|AirportFrom|AirportTo|DayOfWeek|Class|Airline1|AirportFrom1|AirportTo1|
+------+------+------+-------+-----------+---------+---------+-----+--------+------------+----------+
|2313.0|1296.0| 141.0|     DL|        ATL|      HOU|        1|    0|     1.0|         0.0|      33.0|
|6948.0| 360.0| 146.0|     OO|        COS|      ORD|        4|    0|     2.0|        82.0|       1.0|
|1247.0|1170.0| 143.0|     B6|        BOS|      CLT|        3|    0|    12.0|        16.0|      10.0|
|  31.0|1410.0| 344.0|     US|        OGG|      PHX|        6|    0|     5.0|        63.0|       6.0|
| 563.0| 692.0|  98.0|     FL|        BMI|      ATL|        4|    0|    10.0|       139.0|       0.0|
|3692.0| 580.0|  60.0|     WN|        MSY|      BHM|        4|    0|     0.0|        44.0|      64.0|
|1135.0| 690.0| 239.0|     CO|        EWR|      DFW|        4|    0|     9.0|     

In [ ]:
indexed.printSchema()

root
 |-- Flight: double (nullable = true)
 |-- Time: double (nullable = true)
 |-- Length: double (nullable = true)
 |-- Airline: string (nullable = true)
 |-- AirportFrom: string (nullable = true)
 |-- AirportTo: string (nullable = true)
 |-- DayOfWeek: integer (nullable = true)
 |-- Class: integer (nullable = true)
 |-- Airline1: double (nullable = false)
 |-- AirportFrom1: double (nullable = false)
 |-- AirportTo1: double (nullable = false)



In [ ]:
indexed.columns

['Flight',
 'Time',
 'Length',
 'Airline',
 'AirportFrom',
 'AirportTo',
 'DayOfWeek',
 'Class',
 'Airline1',
 'AirportFrom1',
 'AirportTo1']

In [ ]:
assembler=VectorAssembler(inputCols=['Flight','Time','Length','DayOfWeek','Airline1','AirportFrom1','AirportTo1'],outputCol='features')

In [ ]:
output=assembler.transform(indexed)

In [ ]:
output.printSchema()

root
 |-- Flight: double (nullable = true)
 |-- Time: double (nullable = true)
 |-- Length: double (nullable = true)
 |-- Airline: string (nullable = true)
 |-- AirportFrom: string (nullable = true)
 |-- AirportTo: string (nullable = true)
 |-- DayOfWeek: integer (nullable = true)
 |-- Class: integer (nullable = true)
 |-- Airline1: double (nullable = false)
 |-- AirportFrom1: double (nullable = false)
 |-- AirportTo1: double (nullable = false)
 |-- features: vector (nullable = true)



In [ ]:
output.show()

+------+------+------+-------+-----------+---------+---------+-----+--------+------------+----------+--------------------+
|Flight|  Time|Length|Airline|AirportFrom|AirportTo|DayOfWeek|Class|Airline1|AirportFrom1|AirportTo1|            features|
+------+------+------+-------+-----------+---------+---------+-----+--------+------------+----------+--------------------+
|2313.0|1296.0| 141.0|     DL|        ATL|      HOU|        1|    0|     1.0|         0.0|      33.0|[2313.0,1296.0,14...|
|6948.0| 360.0| 146.0|     OO|        COS|      ORD|        4|    0|     2.0|        82.0|       1.0|[6948.0,360.0,146...|
|1247.0|1170.0| 143.0|     B6|        BOS|      CLT|        3|    0|    12.0|        16.0|      10.0|[1247.0,1170.0,14...|
|  31.0|1410.0| 344.0|     US|        OGG|      PHX|        6|    0|     5.0|        63.0|       6.0|[31.0,1410.0,344....|
| 563.0| 692.0|  98.0|     FL|        BMI|      ATL|        4|    0|    10.0|       139.0|       0.0|[563.0,692.0,98.0...|
|3692.0| 580.0| 

In [ ]:
print(output.select("features").show())

+--------------------+
|            features|
+--------------------+
|[2313.0,1296.0,14...|
|[6948.0,360.0,146...|
|[1247.0,1170.0,14...|
|[31.0,1410.0,344....|
|[563.0,692.0,98.0...|
|[3692.0,580.0,60....|
|[1135.0,690.0,239...|
|[1300.0,1210.0,80...|
|[587.0,1295.0,105...|
|[764.0,530.0,108....|
|[1147.0,1103.0,12...|
|[1440.0,951.0,79....|
|[6605.0,1215.0,10...|
|[2670.0,1189.0,11...|
|[1015.0,615.0,142...|
|[7032.0,771.0,70....|
|[138.0,948.0,116....|
|[5411.0,966.0,134...|
|[2517.0,1160.0,12...|
|[3721.0,750.0,119...|
+--------------------+
only showing top 20 rows

None


In [ ]:
final_data=output.select('features','Class')
final_data.show()

+--------------------+-----+
|            features|Class|
+--------------------+-----+
|[2313.0,1296.0,14...|    0|
|[6948.0,360.0,146...|    0|
|[1247.0,1170.0,14...|    0|
|[31.0,1410.0,344....|    0|
|[563.0,692.0,98.0...|    0|
|[3692.0,580.0,60....|    0|
|[1135.0,690.0,239...|    0|
|[1300.0,1210.0,80...|    0|
|[587.0,1295.0,105...|    0|
|[764.0,530.0,108....|    0|
|[1147.0,1103.0,12...|    0|
|[1440.0,951.0,79....|    0|
|[6605.0,1215.0,10...|    0|
|[2670.0,1189.0,11...|    0|
|[1015.0,615.0,142...|    0|
|[7032.0,771.0,70....|    0|
|[138.0,948.0,116....|    0|
|[5411.0,966.0,134...|    0|
|[2517.0,1160.0,12...|    0|
|[3721.0,750.0,119...|    0|
+--------------------+-----+
only showing top 20 rows



## Train and Test split

In [ ]:
train_data,test_data=final_data.randomSplit([0.7,0.3])

In [ ]:
train_data.describe().show()

+-------+------------------+
|summary|             Class|
+-------+------------------+
|  count|            376965|
|   mean|0.4455188147440744|
| stddev| 0.497023596796425|
|    min|                 0|
|    max|                 1|
+-------+------------------+



In [ ]:
test_data.describe().show()

+-------+-------------------+
|summary|              Class|
+-------+-------------------+
|  count|             162417|
|   mean|0.44526742890214693|
| stddev|0.49699684754925944|
|    min|                  0|
|    max|                  1|
+-------+-------------------+



In [ ]:
from pyspark.ml.evaluation import BinaryClassificationEvaluator,MulticlassClassificationEvaluator
binaryEvaluator=BinaryClassificationEvaluator(rawPredictionCol='prediction',labelCol='Class')

In [ ]:
from pyspark.ml.classification import LogisticRegression
classifier=LogisticRegression(maxIter=100,regParam=0.1,threshold=0.4,tol=1e-6,elasticNetParam=0.2,labelCol='Class',featuresCol='features')
model=classifier.fit(train_data)

In [ ]:
pred_data=model.transform(test_data)
pred_data.show(100,False)

+------------------------------------+-----+------------------------------------------+----------------------------------------+----------+
|features                            |Class|rawPrediction                             |probability                             |prediction|
+------------------------------------+-----+------------------------------------------+----------------------------------------+----------+
|[1.0,420.0,60.0,3.0,0.0,39.0,33.0]  |0    |[0.2490611488828749,-0.2490611488828749]  |[0.5619454041540812,0.43805459584591877]|1.0       |
|[1.0,420.0,60.0,3.0,0.0,39.0,33.0]  |1    |[0.2490611488828749,-0.2490611488828749]  |[0.5619454041540812,0.43805459584591877]|1.0       |
|[1.0,420.0,60.0,3.0,0.0,39.0,33.0]  |1    |[0.2490611488828749,-0.2490611488828749]  |[0.5619454041540812,0.43805459584591877]|1.0       |
|[1.0,420.0,60.0,3.0,0.0,39.0,33.0]  |1    |[0.2490611488828749,-0.2490611488828749]  |[0.5619454041540812,0.43805459584591877]|1.0       |
|[1.0,420.0,60.0,4.0

In [ ]:
print(binaryEvaluator.evaluate(pred_data))

0.5615483741090039


Decision Tree Classifier

In [ ]:
from pyspark.ml.classification import DecisionTreeClassifier
dc = DecisionTreeClassifier(featuresCol ="features",labelCol="Class")

In [ ]:
max_bins_value = 300
dt = DecisionTreeClassifier(labelCol="Class", featuresCol="features", maxBins=max_bins_value)

In [ ]:
dc_model = dt.fit(train_data)
y_pred = dc_model.transform(test_data)

In [ ]:
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
mult_eval =MulticlassClassificationEvaluator(labelCol="Class",metricName="accuracy")

In [ ]:
mult_eval.evaluate(y_pred)

0.635586176323907

In [ ]:
# prompt: i need to do prediction my target vaiable is class so instead get input from user and predict whether flight is delay or not and give the code here i have used decision tree classifier model

# Assuming your DecisionTreeClassifier model (dc_model) is already trained as in your provided code.

def predict_flight_delay():
  """Gets flight details from the user and predicts flight delay using the trained model."""

  try:
    flight_number = int(input("Enter Flight Number: "))
    time = int(input("Enter Time: "))
    length = int(input("Enter Length: "))
    day_of_week = int(input("Enter Day of Week (1-7): "))
    airline = input("Enter Airline: ")
    airport_from = input("Enter Airport From: ")
    airport_to = input("Enter Airport To: ")

    # Create a Spark DataFrame with the user input
    import pandas as pd
    data = [[flight_number, time, length, day_of_week, airline, airport_from, airport_to]]
    columns = ['Flight','Time','Length','DayOfWeek','Airline','AirportFrom','AirportTo']
    user_df = spark.createDataFrame(pd.DataFrame(data, columns=columns))

    # Apply the same transformations as your training data
    from pyspark.ml.feature import StringIndexer, VectorAssembler

    indexer = StringIndexer(inputCols=["Airline", "AirportFrom", "AirportTo"],
                             outputCols=["Airline1", "AirportFrom1", "AirportTo1"])
    indexed_user_df = indexer.fit(user_df).transform(user_df)

    assembler = VectorAssembler(inputCols=['Flight', 'Time', 'Length', 'DayOfWeek', 'Airline1', 'AirportFrom1', 'AirportTo1'],
                                outputCol='features')
    assembled_user_df = assembler.transform(indexed_user_df)

    # Make the prediction
    predictions = dc_model.transform(assembled_user_df)
    prediction = predictions.select("prediction").collect()[0][0]

    # Print the prediction
    if prediction == 0.0:
        print("Prediction: Not Delayed")
    else:
        print("Prediction: Delayed")

  except ValueError:
    print("Invalid input. Please enter numeric values for Flight, Time, Length, and DayOfWeek.")
  except Exception as e:
    print(f"An error occurred: {e}")

predict_flight_delay()


Enter Flight Number: 4025
Enter Time: 965
Enter Length: 118
Enter Day of Week (1-7): 4
Enter Airline: 9E
Enter Airport From: ALB
Enter Airport To: DTW
Prediction: Delayed
